Project: /overview/_project.yaml
Book: /overview/_book.yaml

<link rel="stylesheet" href="/site-assets/css/style.css">

<!-- DO NOT EDIT! Automatically generated file. -->


{% comment %}
The source of truth file can be found [here]: http://google3/zz
{% endcomment %}

<div itemscope itemtype="http://developers.google.com/ReferenceObject">
<meta itemprop="name" content="将 <a href="https://www.tensorflow.org/api_docs/python/tf/feature_column"><code>tf.feature_column</code></a> 迁移到 Keras 预处理层" />
<meta itemprop="path" content="Guide & Tutorials" />
<meta itemprop="property" content="tf.compat.v1.data.Dataset"/>
<meta itemprop="property" content="tf.compat.v1.estimator.DNNClassifier"/>
<meta itemprop="property" content="tf.constant"/>
<meta itemprop="property" content="tf.data.Dataset"/>
<meta itemprop="property" content="tf.expand_dims"/>
<meta itemprop="property" content="tf.feature_column.bucketized_column"/>
<meta itemprop="property" content="tf.feature_column.categorical_column_with_identity"/>
<meta itemprop="property" content="tf.feature_column.categorical_column_with_vocabulary_list"/>
<meta itemprop="property" content="tf.feature_column.embedding_column"/>
<meta itemprop="property" content="tf.feature_column.indicator_column"/>
<meta itemprop="property" content="tf.feature_column.numeric_column"/>
<meta itemprop="property" content="tf.feature_column.weighted_categorical_column"/>
<meta itemprop="property" content="tf.keras.Input"/>
<meta itemprop="property" content="tf.keras.Model"/>
<meta itemprop="property" content="tf.keras.layers.CategoryEncoding"/>
<meta itemprop="property" content="tf.keras.layers.Concatenate"/>
<meta itemprop="property" content="tf.keras.layers.Dense"/>
<meta itemprop="property" content="tf.keras.layers.Discretization"/>
<meta itemprop="property" content="tf.keras.layers.Embedding"/>
<meta itemprop="property" content="tf.keras.layers.Normalization"/>
<meta itemprop="property" content="tf.keras.layers.StringLookup"/>
<meta itemprop="property" content="tf.keras.losses.BinaryCrossentropy"/>
<meta itemprop="property" content="tf.keras.saving.load_model"/>
<meta itemprop="property" content="tf.math.reduce_sum"/>
<meta itemprop="property" content="tf.sparse.to_dense"/>
</div>

# 将 <a href="https://www.tensorflow.org/api_docs/python/tf/feature_column"><code>tf.feature_column</code></a> 迁移到 Keras 预处理层

<table class="tfo-notebook-buttons" align="left">
  <td>     <a target="_blank" href="https://tensorflow.google.cn/guide/migrate/migrating_feature_columns"><img src="https://tensorflow.google.cn/images/tf_logo_32px.png">在 TensorFlow.org 上查看</a>   </td>
  <td>     <a target="_blank" href="https://colab.research.google.com/github/tensorflow/docs-l10n/blob/master/site/zh-cn/guide/migrate/migrating_feature_columns.ipynb"><img src="https://tensorflow.google.cn/images/colab_logo_32px.png">在 Google Colab 中运行</a> </td>
  <td>     <a target="_blank" href="https://github.com/tensorflow/docs-l10n/blob/master/site/zh-cn/guide/migrate/migrating_feature_columns.ipynb"><img src="https://tensorflow.google.cn/images/GitHub-Mark-32px.png">在 GitHub 上查看源代码</a> </td>
  <td>     <a href="https://storage.googleapis.com/tensorflow_docs/docs-l10n/site/zh-cn/guide/migrate/migrating_feature_columns.ipynb"><img src="https://tensorflow.google.cn/images/download_logo_32px.png">下载笔记本</a>   </td>
</table>

训练模型通常会伴随一些特征预处理，尤其是在处理结构化数据时。在 TensorFlow 1 中训练 <a href="https://www.tensorflow.org/api_docs/python/tf/estimator/Estimator"><code>tf.estimator.Estimator</code></a> 时，通常使用 <a href="https://www.tensorflow.org/api_docs/python/tf/feature_column"><code>tf.feature_column</code></a> API 执行特征预处理。在 TensorFlow 2 中，您可以直接使用 Keras 预处理层执行此操作。

本迁移指南演示了使用特征列和预处理层的常见特征转换，然后使用这两种 API 训练一个完整的模型。

首先，从几个必要的导入开始：

In [2]:
import tensorflow as tf
import tensorflow.compat.v1 as tf1
import math

2023-11-07 19:43:44.933552: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2023-11-07 19:43:44.933604: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2023-11-07 19:43:44.935149: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered


接下来，添加一个用于调用特征列的效用函数进行演示：

In [3]:
def call_feature_columns(feature_columns, inputs):
  # This is a convenient way to call a `feature_column` outside of an estimator
  # to display its output.
  feature_layer = tf1.keras.layers.DenseFeatures(feature_columns)
  return feature_layer(inputs)

## 输入处理

要将特征列与 Estimator 一起使用，模型输入始终应为张量的字典：

In [4]:
input_dict = {
  'foo': tf.constant([1]),
  'bar': tf.constant([0]),
  'baz': tf.constant([-1])
}

每个特征列都需要有一个键来索引到源数据。所有特征列的输出串联并由 Estimator 模型使用。

In [5]:
columns = [
  tf1.feature_column.numeric_column('foo'),
  tf1.feature_column.numeric_column('bar'),
  tf1.feature_column.numeric_column('baz'),
]
call_feature_columns(columns, input_dict)

Instructions for updating:
Use Keras preprocessing layers instead, either directly or via the `tf.keras.utils.FeatureSpace` utility. Each of `tf.feature_column.*` has a functional equivalent in `tf.keras.layers` for feature preprocessing when training a Keras model.


<tf.Tensor: shape=(1, 3), dtype=float32, numpy=array([[ 0., -1.,  1.]], dtype=float32)>

在 Keras 中，模型输入更加灵活。<a href="https://www.tensorflow.org/api_docs/python/tf/keras/Model"><code>tf.keras.Model</code></a> 可以处理单个张量输入、张量特征列表或张量特征字典。可以通过在模型创建时传递 <a href="https://www.tensorflow.org/api_docs/python/tf/keras/Input"><code>tf.keras.Input</code></a> 的字典来处理字典输入。输入不会自动串联，这样它们便能以更灵活的方式使用。它们可以与 <a href="https://www.tensorflow.org/api_docs/python/tf/keras/layers/Concatenate"><code>tf.keras.layers.Concatenate</code></a> 串联。

In [6]:
inputs = {
  'foo': tf.keras.Input(shape=()),
  'bar': tf.keras.Input(shape=()),
  'baz': tf.keras.Input(shape=()),
}
# Inputs are typically transformed by preprocessing layers before concatenation.
outputs = tf.keras.layers.Concatenate()(inputs.values())
model = tf.keras.Model(inputs=inputs, outputs=outputs)
model(input_dict)

<tf.Tensor: shape=(3,), dtype=float32, numpy=array([ 1.,  0., -1.], dtype=float32)>

## 独热编码整数 ID

常见的特征转换是对已知范围内的整数输入进行独热编码。下面是一个使用特征列的示例：

In [7]:
categorical_col = tf1.feature_column.categorical_column_with_identity(
    'type', num_buckets=3)
indicator_col = tf1.feature_column.indicator_column(categorical_col)
call_feature_columns(indicator_col, {'type': [0, 1, 2]})

Instructions for updating:
Use Keras preprocessing layers instead, either directly or via the `tf.keras.utils.FeatureSpace` utility. Each of `tf.feature_column.*` has a functional equivalent in `tf.keras.layers` for feature preprocessing when training a Keras model.


Instructions for updating:
Use Keras preprocessing layers instead, either directly or via the `tf.keras.utils.FeatureSpace` utility. Each of `tf.feature_column.*` has a functional equivalent in `tf.keras.layers` for feature preprocessing when training a Keras model.


<tf.Tensor: shape=(3, 3), dtype=float32, numpy=
array([[1., 0., 0.],
       [0., 1., 0.],
       [0., 0., 1.]], dtype=float32)>

利用 Keras 预处理层，这些列可被替换为单个 <a href="https://www.tensorflow.org/api_docs/python/tf/keras/layers/CategoryEncoding"><code>tf.keras.layers.CategoryEncoding</code></a> 层，其中 `output_mode` 设置为 `'one_hot'`：

In [8]:
one_hot_layer = tf.keras.layers.CategoryEncoding(
    num_tokens=3, output_mode='one_hot')
one_hot_layer([0, 1, 2])

<tf.Tensor: shape=(3, 3), dtype=float32, numpy=
array([[1., 0., 0.],
       [0., 1., 0.],
       [0., 0., 1.]], dtype=float32)>

注：对于大型独热编码，使用输出的稀疏表示会更高效。如果将 `sparse=True` 传递给 `CategoryEncoding` 层，则该层的输出将是 <a href="https://www.tensorflow.org/api_docs/python/tf/sparse/SparseTensor"><code>tf.sparse.SparseTensor</code></a>，它可以作为 <a href="https://www.tensorflow.org/api_docs/python/tf/keras/layers/Dense"><code>tf.keras.layers.Dense</code></a> 层的输入高效地处理。

## 归一化数字特征

在处理具有特征列的连续浮点特征时，需要使用 <a href="https://www.tensorflow.org/api_docs/python/tf/feature_column/numeric_column"><code>tf.feature_column.numeric_column</code></a>。在输入已经归一化的情况下，将其转换为 Keras 的操作十分简单。可以直接在模型中使用 <a href="https://www.tensorflow.org/api_docs/python/tf/keras/Input"><code>tf.keras.Input</code></a>，如上面所示。

`numeric_column` 也可用于归一化输入：

In [9]:
def normalize(x):
  mean, variance = (2.0, 1.0)
  return (x - mean) / math.sqrt(variance)
numeric_col = tf1.feature_column.numeric_column('col', normalizer_fn=normalize)
call_feature_columns(numeric_col, {'col': tf.constant([[0.], [1.], [2.]])})

<tf.Tensor: shape=(3, 1), dtype=float32, numpy=
array([[-2.],
       [-1.],
       [ 0.]], dtype=float32)>

相比之下，使用 Keras，这种归一化可以使用 <a href="https://www.tensorflow.org/api_docs/python/tf/keras/layers/Normalization"><code>tf.keras.layers.Normalization</code></a> 完成。

In [10]:
normalization_layer = tf.keras.layers.Normalization(mean=2.0, variance=1.0)
normalization_layer(tf.constant([[0.], [1.], [2.]]))

<tf.Tensor: shape=(3, 1), dtype=float32, numpy=
array([[-2.],
       [-1.],
       [ 0.]], dtype=float32)>

## 对数字特征进行分桶和独热编码

连续浮点输入的另一种常见转换是分桶为固定范围的整数。

在特征列中，可以使用 <a href="https://www.tensorflow.org/api_docs/python/tf/feature_column/bucketized_column"><code>tf.feature_column.bucketized_column</code></a> 实现：

In [11]:
numeric_col = tf1.feature_column.numeric_column('col')
bucketized_col = tf1.feature_column.bucketized_column(numeric_col, [1, 4, 5])
call_feature_columns(bucketized_col, {'col': tf.constant([1., 2., 3., 4., 5.])})


Instructions for updating:
Use Keras preprocessing layers instead, either directly or via the `tf.keras.utils.FeatureSpace` utility. Each of `tf.feature_column.*` has a functional equivalent in `tf.keras.layers` for feature preprocessing when training a Keras model.


<tf.Tensor: shape=(5, 4), dtype=float32, numpy=
array([[0., 1., 0., 0.],
       [0., 1., 0., 0.],
       [0., 1., 0., 0.],
       [0., 0., 1., 0.],
       [0., 0., 0., 1.]], dtype=float32)>

在 Keras 中，可以使用 <a href="https://www.tensorflow.org/api_docs/python/tf/keras/layers/Discretization"><code>tf.keras.layers.Discretization</code></a> 代替：

In [12]:
discretization_layer = tf.keras.layers.Discretization(bin_boundaries=[1, 4, 5])
one_hot_layer = tf.keras.layers.CategoryEncoding(
    num_tokens=4, output_mode='one_hot')
one_hot_layer(discretization_layer([1., 2., 3., 4., 5.]))

<tf.Tensor: shape=(5, 4), dtype=float32, numpy=
array([[0., 1., 0., 0.],
       [0., 1., 0., 0.],
       [0., 1., 0., 0.],
       [0., 0., 1., 0.],
       [0., 0., 0., 1.]], dtype=float32)>

## 使用词汇表对字符串数据进行独热编码

处理字符串特征通常需要词汇查找来将字符串转换为索引。下面是一个使用特征列查找字符串，然后对索引进行独热编码的示例：

In [13]:
vocab_col = tf1.feature_column.categorical_column_with_vocabulary_list(
    'sizes',
    vocabulary_list=['small', 'medium', 'large'],
    num_oov_buckets=0)
indicator_col = tf1.feature_column.indicator_column(vocab_col)
call_feature_columns(indicator_col, {'sizes': ['small', 'medium', 'large']})

Instructions for updating:
Use Keras preprocessing layers instead, either directly or via the `tf.keras.utils.FeatureSpace` utility. Each of `tf.feature_column.*` has a functional equivalent in `tf.keras.layers` for feature preprocessing when training a Keras model.


<tf.Tensor: shape=(3, 3), dtype=float32, numpy=
array([[1., 0., 0.],
       [0., 1., 0.],
       [0., 0., 1.]], dtype=float32)>

利用 Keras 预处理层，可以使用 <a href="https://www.tensorflow.org/api_docs/python/tf/keras/layers/StringLookup"><code>tf.keras.layers.StringLookup</code></a> 层，并将 `output_mode` 设置为 `'one_hot'`：

In [14]:
string_lookup_layer = tf.keras.layers.StringLookup(
    vocabulary=['small', 'medium', 'large'],
    num_oov_indices=0,
    output_mode='one_hot')
string_lookup_layer(['small', 'medium', 'large'])

<tf.Tensor: shape=(3, 3), dtype=float32, numpy=
array([[1., 0., 0.],
       [0., 1., 0.],
       [0., 0., 1.]], dtype=float32)>

注：对于大型独热编码，使用输出的稀疏表示会更高效。如果将 `sparse=True` 传递给 `StringLookup` 层，则该层的输出将是 <a href="https://www.tensorflow.org/api_docs/python/tf/sparse/SparseTensor"><code>tf.sparse.SparseTensor</code></a>，它可以作为 <a href="https://www.tensorflow.org/api_docs/python/tf/keras/layers/Dense"><code>tf.keras.layers.Dense</code></a> 层的输入高效地处理。

## 使用词汇表嵌入字符串数据

对于较大的词汇表，通常需要嵌入向量才能获得良好的性能。下面是一个使用特征列嵌入字符串特征的示例：

In [15]:
vocab_col = tf1.feature_column.categorical_column_with_vocabulary_list(
    'col',
    vocabulary_list=['small', 'medium', 'large'],
    num_oov_buckets=0)
embedding_col = tf1.feature_column.embedding_column(vocab_col, 4)
call_feature_columns(embedding_col, {'col': ['small', 'medium', 'large']})

Instructions for updating:
Use Keras preprocessing layers instead, either directly or via the `tf.keras.utils.FeatureSpace` utility. Each of `tf.feature_column.*` has a functional equivalent in `tf.keras.layers` for feature preprocessing when training a Keras model.


<tf.Tensor: shape=(3, 4), dtype=float32, numpy=
array([[-0.00123898, -0.29734045,  0.79748577, -0.60346466],
       [ 0.6792554 ,  0.9402996 ,  0.18042608,  0.98339444],
       [ 0.14242958, -0.01956465,  0.945728  , -0.3963206 ]],
      dtype=float32)>

利用 Keras 预处理层，可以通过组合 <a href="https://www.tensorflow.org/api_docs/python/tf/keras/layers/StringLookup"><code>tf.keras.layers.StringLookup</code></a> 层和 <a href="https://www.tensorflow.org/api_docs/python/tf/keras/layers/Embedding"><code>tf.keras.layers.Embedding</code></a> 层来实现。`StringLookup` 的默认输出将是可直接馈送到嵌入向量中的整数索引。

注：`Embedding` 层包含可训练参数。虽然 `StringLookup` 层可以应用于模型内部或外部的数据，但 `Embedding` 必须始终是可训练 Keras 模型的一部分才能正确训练。

In [16]:
string_lookup_layer = tf.keras.layers.StringLookup(
    vocabulary=['small', 'medium', 'large'], num_oov_indices=0)
embedding = tf.keras.layers.Embedding(3, 4)
embedding(string_lookup_layer(['small', 'medium', 'large']))

<tf.Tensor: shape=(3, 4), dtype=float32, numpy=
array([[ 0.02012427,  0.02538512,  0.0153519 , -0.03949844],
       [ 0.03889913,  0.0438555 ,  0.03012307, -0.00586962],
       [ 0.01025263, -0.04199063,  0.01492839,  0.01071114]],
      dtype=float32)>

## 对加权分类数据求和

在某些情况下，您需要处理分类数据，其中类别的每次出现都附带关联的权重。在特征列中，这由 <a href="https://www.tensorflow.org/api_docs/python/tf/feature_column/weighted_categorical_column"><code>tf.feature_column.weighted_categorical_column</code></a> 处理。与 `indicator_column` 配对时，效果是对每个类别的权重求和。

In [17]:
ids = tf.constant([[5, 11, 5, 17, 17]])
weights = tf.constant([[0.5, 1.5, 0.7, 1.8, 0.2]])

categorical_col = tf1.feature_column.categorical_column_with_identity(
    'ids', num_buckets=20)
weighted_categorical_col = tf1.feature_column.weighted_categorical_column(
    categorical_col, 'weights')
indicator_col = tf1.feature_column.indicator_column(weighted_categorical_col)
call_feature_columns(indicator_col, {'ids': ids, 'weights': weights})

Instructions for updating:
Use Keras preprocessing layers instead, either directly or via the `tf.keras.utils.FeatureSpace` utility. Each of `tf.feature_column.*` has a functional equivalent in `tf.keras.layers` for feature preprocessing when training a Keras model.


Instructions for updating:
No similar op available at this time.


<tf.Tensor: shape=(1, 20), dtype=float32, numpy=
array([[0. , 0. , 0. , 0. , 0. , 1.2, 0. , 0. , 0. , 0. , 0. , 1.5, 0. ,
        0. , 0. , 0. , 0. , 2. , 0. , 0. ]], dtype=float32)>

在 Keras 中，这可以通过将 `count_weights` 输入传递给 <a href="https://www.tensorflow.org/api_docs/python/tf/keras/layers/CategoryEncoding"><code>tf.keras.layers.CategoryEncoding</code></a> 来完成，其中 `output_mode='count'`。

In [18]:
ids = tf.constant([[5, 11, 5, 17, 17]])
weights = tf.constant([[0.5, 1.5, 0.7, 1.8, 0.2]])

# Using sparse output is more efficient when `num_tokens` is large.
count_layer = tf.keras.layers.CategoryEncoding(
    num_tokens=20, output_mode='count', sparse=True)
tf.sparse.to_dense(count_layer(ids, count_weights=weights))

<tf.Tensor: shape=(1, 20), dtype=float32, numpy=
array([[0. , 0. , 0. , 0. , 0. , 1.2, 0. , 0. , 0. , 0. , 0. , 1.5, 0. ,
        0. , 0. , 0. , 0. , 2. , 0. , 0. ]], dtype=float32)>

## 嵌入加权分类数据

您可能还想嵌入加权分类输入。在特征列中， `embedding_column` 包含 `combiner` 参数。如果任何样本包含一个类别的多个条目，则它们将根据参数设置进行组合（默认为 `'mean'`）。

In [19]:
ids = tf.constant([[5, 11, 5, 17, 17]])
weights = tf.constant([[0.5, 1.5, 0.7, 1.8, 0.2]])

categorical_col = tf1.feature_column.categorical_column_with_identity(
    'ids', num_buckets=20)
weighted_categorical_col = tf1.feature_column.weighted_categorical_column(
    categorical_col, 'weights')
embedding_col = tf1.feature_column.embedding_column(
    weighted_categorical_col, 4, combiner='mean')
call_feature_columns(embedding_col, {'ids': ids, 'weights': weights})

<tf.Tensor: shape=(1, 4), dtype=float32, numpy=
array([[-0.43430573, -0.22497068,  0.15360786, -0.29884622]],
      dtype=float32)>

在 Keras 中，<a href="https://www.tensorflow.org/api_docs/python/tf/keras/layers/Embedding"><code>tf.keras.layers.Embedding</code></a> 没有 `combiner` 选项，但可以使用 <a href="https://www.tensorflow.org/api_docs/python/tf/keras/layers/Dense"><code>tf.keras.layers.Dense</code></a> 实现相同的效果。上面的 `embedding_column` 只是根据类别权重线性组合嵌入向量。虽然一开始并不明显，但它完全等效于将您的分类输入表示为大小为 `(num_tokens)` 的稀疏权重向量，随后将它们乘以形状为 `(embedding_size, num_tokens)` 的 `Dense` 内核 。

In [20]:
ids = tf.constant([[5, 11, 5, 17, 17]])
weights = tf.constant([[0.5, 1.5, 0.7, 1.8, 0.2]])

# For `combiner='mean'`, normalize your weights to sum to 1. Removing this line
# would be equivalent to an `embedding_column` with `combiner='sum'`.
weights = weights / tf.reduce_sum(weights, axis=-1, keepdims=True)

count_layer = tf.keras.layers.CategoryEncoding(
    num_tokens=20, output_mode='count', sparse=True)
embedding_layer = tf.keras.layers.Dense(4, use_bias=False)
embedding_layer(count_layer(ids, count_weights=weights))

<tf.Tensor: shape=(1, 4), dtype=float32, numpy=
array([[-0.04466075, -0.20848304, -0.07644258, -0.15684158]],
      dtype=float32)>

## 完整的训练示例

为了展示完整的训练工作流，首先准备一些具有三种不同类型特征的数据：

In [21]:
features = {
    'type': [0, 1, 1],
    'size': ['small', 'small', 'medium'],
    'weight': [2.7, 1.8, 1.6],
}
labels = [1, 1, 0]
predict_features = {'type': [0], 'size': ['foo'], 'weight': [-0.7]}

为 TensorFlow 1 和 TensorFlow 2 工作流定义一些通用常量：

In [22]:
vocab = ['small', 'medium', 'large']
one_hot_dims = 3
embedding_dims = 4
weight_mean = 2.0
weight_variance = 1.0

### 使用特征列

特征列在创建时必须作为列表传递给 Estimator，并在训练期间隐式调用。

In [23]:
categorical_col = tf1.feature_column.categorical_column_with_identity(
    'type', num_buckets=one_hot_dims)
# Convert index to one-hot; e.g. [2] -> [0,0,1].
indicator_col = tf1.feature_column.indicator_column(categorical_col)

# Convert strings to indices; e.g. ['small'] -> [1].
vocab_col = tf1.feature_column.categorical_column_with_vocabulary_list(
    'size', vocabulary_list=vocab, num_oov_buckets=1)
# Embed the indices.
embedding_col = tf1.feature_column.embedding_column(vocab_col, embedding_dims)

normalizer_fn = lambda x: (x - weight_mean) / math.sqrt(weight_variance)
# Normalize the numeric inputs; e.g. [2.0] -> [0.0].
numeric_col = tf1.feature_column.numeric_column(
    'weight', normalizer_fn=normalizer_fn)

estimator = tf1.estimator.DNNClassifier(
    feature_columns=[indicator_col, embedding_col, numeric_col],
    hidden_units=[1])

def _input_fn():
  return tf1.data.Dataset.from_tensor_slices((features, labels)).batch(1)

estimator.train(_input_fn)

Instructions for updating:
Use tf.keras instead.


Instructions for updating:
Use tf.keras instead.


Instructions for updating:
Use tf.keras instead.


INFO:tensorflow:Using default config.


INFO:tensorflow:Using config: {'_model_dir': '/tmpfs/tmp/tmplya27c6i', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': None, '_save_checkpoints_secs': 600, '_session_config': allow_soft_placement: true
graph_options {
  rewrite_options {
    meta_optimizer_iterations: ONE
  }
}
, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': 100, '_train_distribute': None, '_device_fn': None, '_protocol': None, '_eval_distribute': None, '_experimental_distribute': None, '_experimental_max_worker_delay_secs': None, '_session_creation_timeout_secs': 7200, '_checkpoint_save_graph_def': True, '_service': None, '_cluster_spec': ClusterSpec({}), '_task_type': 'worker', '_task_id': 0, '_global_id_in_cluster': 0, '_master': '', '_evaluation_master': '', '_is_chief': True, '_num_ps_replicas': 0, '_num_worker_replicas': 1}


...

INFO:tensorflow:loss = 0.23499121, step = 0


INFO:tensorflow:Calling checkpoint listeners before saving checkpoint 3...


INFO:tensorflow:Saving checkpoints for 3 into /tmpfs/tmp/tmplya27c6i/model.ckpt.


INFO:tensorflow:Calling checkpoint listeners after saving checkpoint 3...


INFO:tensorflow:Loss for final step: 0.7172243.


在模型上运行推断时，特征列也将用于转换输入数据。

In [24]:
def _predict_fn():
  return tf1.data.Dataset.from_tensor_slices(predict_features).batch(1)

next(estimator.predict(_predict_fn))

INFO:tensorflow:Calling model_fn.


Instructions for updating:
Use tf.keras instead.


Instructions for updating:
Use tf.keras instead.


Instructions for updating:
Use tf.keras instead.


INFO:tensorflow:Done calling model_fn.


INFO:tensorflow:Graph was finalized.


INFO:tensorflow:Restoring parameters from /tmpfs/tmp/tmplya27c6i/model.ckpt-3


INFO:tensorflow:Running local_init_op.


INFO:tensorflow:Done running local_init_op.


{'logits': array([0.00870242], dtype=float32),
 'logistic': array([0.50217557], dtype=float32),
 'probabilities': array([0.4978244 , 0.50217557], dtype=float32),
 'class_ids': array([1]),
 'classes': array([b'1'], dtype=object),
 'all_class_ids': array([0, 1], dtype=int32),
 'all_classes': array([b'0', b'1'], dtype=object)}

### 使用 Keras 预处理层

Keras 预处理层在调用它们的位置上更加灵活。层可以直接应用于张量，在 <a href="https://www.tensorflow.org/api_docs/python/tf/data"><code>tf.data</code></a> 输入流水线内使用，或者直接构建到可训练的 Keras 模型中。

在此示例中，您将在 <a href="https://www.tensorflow.org/api_docs/python/tf/data"><code>tf.data</code></a> 输入流水线中应用预处理层。为此，可以定义一个单独的 <a href="https://www.tensorflow.org/api_docs/python/tf/keras/Model"><code>tf.keras.Model</code></a> 来预处理您的输入特征。此模型不可训练，但可以方便地对预处理层进行分组。

In [25]:
inputs = {
  'type': tf.keras.Input(shape=(), dtype='int64'),
  'size': tf.keras.Input(shape=(), dtype='string'),
  'weight': tf.keras.Input(shape=(), dtype='float32'),
}
# Convert index to one-hot; e.g. [2] -> [0,0,1].
type_output = tf.keras.layers.CategoryEncoding(
      one_hot_dims, output_mode='one_hot')(inputs['type'])
# Convert size strings to indices; e.g. ['small'] -> [1].
size_output = tf.keras.layers.StringLookup(vocabulary=vocab)(inputs['size'])
# Normalize the numeric inputs; e.g. [2.0] -> [0.0].
weight_output = tf.keras.layers.Normalization(
      axis=None, mean=weight_mean, variance=weight_variance)(inputs['weight'])
outputs = {
  'type': type_output,
  'size': size_output,
  'weight': weight_output,
}
preprocessing_model = tf.keras.Model(inputs, outputs)

注：作为在层创建时提供词汇表和归一化统计信息的替代方式，许多预处理层提供了一个 `adapt()` 方法，可用于直接从输入数据学习层状态。请参阅[预处理指南](https://tensorflow.google.cn/guide/keras/preprocessing_layers#the_adapt_method) ，了解更多详细信息。

您现在可以在对 <a href="https://www.tensorflow.org/api_docs/python/tf/data/Dataset#map"><code>tf.data.Dataset.map</code></a> 的调用中应用此模型。请注意，传递给 `map` 的函数将自动转换为 <a href="https://www.tensorflow.org/api_docs/python/tf/function"><code>tf.function</code></a>，并且用于编写 <a href="https://www.tensorflow.org/api_docs/python/tf/function"><code>tf.function</code></a> 代码的通常注意事项适用（无副作用）。

In [26]:
# Apply the preprocessing in tf.data.Dataset.map.
dataset = tf.data.Dataset.from_tensor_slices((features, labels)).batch(1)
dataset = dataset.map(lambda x, y: (preprocessing_model(x), y),
                      num_parallel_calls=tf.data.AUTOTUNE)
# Display a preprocessed input sample.
next(dataset.take(1).as_numpy_iterator())

({'type': array([[1., 0., 0.]], dtype=float32),
  'size': array([1]),
  'weight': array([0.70000005], dtype=float32)},
 array([1], dtype=int32))

接下来，可以定义一个包含可训练层的单独 `Model`。请注意此模型的输入现在如何反映预处理的特征类型和形状。

In [27]:
inputs = {
  'type': tf.keras.Input(shape=(one_hot_dims,), dtype='float32'),
  'size': tf.keras.Input(shape=(), dtype='int64'),
  'weight': tf.keras.Input(shape=(), dtype='float32'),
}
# Since the embedding is trainable, it needs to be part of the training model.
embedding = tf.keras.layers.Embedding(len(vocab), embedding_dims)
outputs = tf.keras.layers.Concatenate()([
  inputs['type'],
  embedding(inputs['size']),
  tf.expand_dims(inputs['weight'], -1),
])
outputs = tf.keras.layers.Dense(1)(outputs)
training_model = tf.keras.Model(inputs, outputs)

您现在可以使用 <a href="https://www.tensorflow.org/api_docs/python/tf/keras/Model#fit"><code>tf.keras.Model.fit</code></a> 训练 `training_model`。

In [28]:
# Train on the preprocessed data.
training_model.compile(
    loss=tf.keras.losses.BinaryCrossentropy(from_logits=True))
training_model.fit(dataset)

3/3 [==============================] - 1s 5ms/step - loss: 0.5726


I0000 00:00:1699386236.696100  211480 device_compiler.h:186] Compiled cluster using XLA!  This line is logged at most once for the lifetime of the process.


最后，在推断时，不妨将这些单独的阶段组合成处理原始特征输入的单一模型。

In [29]:
inputs = preprocessing_model.input
outputs = training_model(preprocessing_model(inputs))
inference_model = tf.keras.Model(inputs, outputs)

predict_dataset = tf.data.Dataset.from_tensor_slices(predict_features).batch(1)
inference_model.predict(predict_dataset)

1/1 [==============================] - 0s 108ms/step


array([[-1.4377327]], dtype=float32)

可以将此组合模型保存为 <a>.keras</a> 文件供以后使用。

In [30]:
inference_model.save('model.keras')
restored_model = tf.keras.models.load_model('model.keras')
restored_model.predict(predict_dataset)

1/1 [==============================] - 0s 82ms/step


array([[-1.4377327]], dtype=float32)

注：预处理层不可训练，这允许您使用 <code>tf.data</code> <em>异步</em>应用它们。这样做可以获得性能优势，因为您既可以预提取预处理的批次，又可以释放任何加速器以专注于模型的可微分部分（请在<a data-md-type="raw_html" href="../data_performance.ipynb">使用 <code>tf.data</code> API 提升性能</a>指南的<em>预提取</em>部分了解更多信息）。如本指南中所示，在训练期间分离预处理并在推断期间组合预处理是一种利用这些性能提升的灵活方式。但是，如果您的模型很小或预处理时间可以忽略不计，那么从一开始就将预处理构建为一个完整的模型可能会更简单。为此，您可以从 <a href="https://www.tensorflow.org/api_docs/python/tf/keras/Input"><code>tf.keras.Input</code></a> 开始构建单一模型，接着是预处理层，最后是可训练层。

## 特征列对应关系表

作为参考，下面是特征列和 Keras 预处理层之间的大致对应关系：

<table>
<div>  <tr>
    <th>特征列</th>
    <th>Keras 层</th>
  </tr>
  <tr>
    <td><a href="https://www.tensorflow.org/api_docs/python/tf/feature_column/bucketized_column"><code>tf.feature_column.bucketized_column</code></a></td>
    <td><a href="https://www.tensorflow.org/api_docs/python/tf/keras/layers/Discretization"><code>tf.keras.layers.Discretization</code></a></td>
  </tr>
  <tr>
    <td><a href="https://www.tensorflow.org/api_docs/python/tf/feature_column/categorical_column_with_hash_bucket"><code>tf.feature_column.categorical_column_with_hash_bucket</code></a></td>
    <td><a href="https://www.tensorflow.org/api_docs/python/tf/keras/layers/Hashing"><code>tf.keras.layers.Hashing</code></a></td>
  </tr>
  <tr>
    <td><a href="https://www.tensorflow.org/api_docs/python/tf/feature_column/categorical_column_with_identity"><code>tf.feature_column.categorical_column_with_identity</code></a></td>
    <td><a href="https://www.tensorflow.org/api_docs/python/tf/keras/layers/CategoryEncoding"><code>tf.keras.layers.CategoryEncoding</code></a></td>
  </tr>
  <tr>
    <td><a href="https://www.tensorflow.org/api_docs/python/tf/feature_column/categorical_column_with_vocabulary_file"><code>tf.feature_column.categorical_column_with_vocabulary_file</code></a></td>
    <td><a href="https://www.tensorflow.org/api_docs/python/tf/keras/layers/StringLookup"><code>tf.keras.layers.StringLookup</code></a> 或 <a href="https://www.tensorflow.org/api_docs/python/tf/keras/layers/IntegerLookup"><code>tf.keras.layers.IntegerLookup</code></a></td>
  </tr>
  <tr>
    <td><a href="https://www.tensorflow.org/api_docs/python/tf/feature_column/categorical_column_with_vocabulary_list"><code>tf.feature_column.categorical_column_with_vocabulary_list</code></a></td>
    <td><a href="https://www.tensorflow.org/api_docs/python/tf/keras/layers/StringLookup"><code>tf.keras.layers.StringLookup</code></a> 或 <a href="https://www.tensorflow.org/api_docs/python/tf/keras/layers/IntegerLookup"><code>tf.keras.layers.IntegerLookup</code></a></td>
  </tr>
  <tr>
    <td><a href="https://www.tensorflow.org/api_docs/python/tf/feature_column/crossed_column"><code>tf.feature_column.crossed_column</code></a></td>
    <td><a href="https://www.tensorflow.org/api_docs/python/tf/keras/layers/HashedCrossing"><code>tf.keras.layers.experimental.preprocessing.HashedCrossing</code></a></td>
  </tr>
  <tr>
    <td><a href="https://www.tensorflow.org/api_docs/python/tf/feature_column/embedding_column"><code>tf.feature_column.embedding_column</code></a></td>
    <td><a href="https://www.tensorflow.org/api_docs/python/tf/keras/layers/Embedding"><code>tf.keras.layers.Embedding</code></a></td>
  </tr>
  <tr>
    <td><a href="https://www.tensorflow.org/api_docs/python/tf/feature_column/indicator_column"><code>tf.feature_column.indicator_column</code></a></td>
    <td>`output_mode='one_hot'` 或 `output_mode='multi_hot'`*</td>
  </tr>
  <tr>
    <td><a href="https://www.tensorflow.org/api_docs/python/tf/feature_column/numeric_column"><code>tf.feature_column.numeric_column</code></a></td>
    <td><a href="https://www.tensorflow.org/api_docs/python/tf/keras/layers/Normalization"><code>tf.keras.layers.Normalization</code></a></td>
  </tr>
  <tr>
    <td><a href="https://www.tensorflow.org/api_docs/python/tf/feature_column/sequence_categorical_column_with_hash_bucket"><code>tf.feature_column.sequence_categorical_column_with_hash_bucket</code></a></td>
    <td><a href="https://www.tensorflow.org/api_docs/python/tf/keras/layers/Hashing"><code>tf.keras.layers.Hashing</code></a></td>
  </tr>
  <tr>
    <td><a href="https://www.tensorflow.org/api_docs/python/tf/feature_column/sequence_categorical_column_with_identity"><code>tf.feature_column.sequence_categorical_column_with_identity</code></a></td>
    <td><a href="https://www.tensorflow.org/api_docs/python/tf/keras/layers/CategoryEncoding"><code>tf.keras.layers.CategoryEncoding</code></a></td>
  </tr>
  <tr>
    <td><a href="https://www.tensorflow.org/api_docs/python/tf/feature_column/sequence_categorical_column_with_vocabulary_file"><code>tf.feature_column.sequence_categorical_column_with_vocabulary_file</code></a></td>
    <td><a href="https://www.tensorflow.org/api_docs/python/tf/keras/layers/StringLookup"><code>tf.keras.layers.StringLookup</code></a>、<a href="https://www.tensorflow.org/api_docs/python/tf/keras/layers/IntegerLookup"><code>tf.keras.layers.IntegerLookup</code></a> 或 `tf.keras.layer.TextVectorization`†</td>
  </tr>
  <tr>
    <td><a href="https://www.tensorflow.org/api_docs/python/tf/feature_column/sequence_categorical_column_with_vocabulary_list"><code>tf.feature_column.sequence_categorical_column_with_vocabulary_list</code></a></td>
    <td><a href="https://www.tensorflow.org/api_docs/python/tf/keras/layers/StringLookup"><code>tf.keras.layers.StringLookup</code></a>、<a href="https://www.tensorflow.org/api_docs/python/tf/keras/layers/IntegerLookup"><code>tf.keras.layers.IntegerLookup</code></a> 或 `tf.keras.layer.TextVectorization`†</td>
  </tr>
  <tr>
    <td><a href="https://www.tensorflow.org/api_docs/python/tf/feature_column/sequence_numeric_column"><code>tf.feature_column.sequence_numeric_column</code></a></td>
    <td><a href="https://www.tensorflow.org/api_docs/python/tf/keras/layers/Normalization"><code>tf.keras.layers.Normalization</code></a></td>
  </tr>
  <tr>
    <td><a href="https://www.tensorflow.org/api_docs/python/tf/feature_column/weighted_categorical_column"><code>tf.feature_column.weighted_categorical_column</code></a></td>
    <td><a href="https://www.tensorflow.org/api_docs/python/tf/keras/layers/CategoryEncoding"><code>tf.keras.layers.CategoryEncoding</code></a></td>
  </tr>
</div>
</table>

* `output_mode` 可以传递给 <a href="https://www.tensorflow.org/api_docs/python/tf/keras/layers/CategoryEncoding"><code>tf.keras.layers.CategoryEncoding</code></a>、<a href="https://www.tensorflow.org/api_docs/python/tf/keras/layers/StringLookup"><code>tf.keras.layers.StringLookup</code></a>、<a href="https://www.tensorflow.org/api_docs/python/tf/keras/layers/IntegerLookup"><code>tf.keras.layers.IntegerLookup</code></a> 和 <a href="https://www.tensorflow.org/api_docs/python/tf/keras/layers/TextVectorization"><code>tf.keras.layers.TextVectorization</code></a>。

† <a href="https://www.tensorflow.org/api_docs/python/tf/keras/layers/TextVectorization"><code>tf.keras.layers.TextVectorization</code></a> 可以直接处理自由格式的文本输入（例如，整个句子或段落）。这不是 TensorFlow 1 中分类序列处理的一对一替代，但可以为临时文本预处理提供方便的替代。

注：线性 Estimator（例如 <a href="https://www.tensorflow.org/api_docs/python/tf/estimator/LinearClassifier"><code>tf.estimator.LinearClassifier</code></a>）可以在没有 `embedding_column` 或 `indicator_column` 的情况下处理直接分类输入（整数索引）。但是，整数索引不能直接传递给 <a href="https://www.tensorflow.org/api_docs/python/tf/keras/layers/Dense"><code>tf.keras.layers.Dense</code></a> 或 <a href="https://www.tensorflow.org/api_docs/python/tf/keras/experimental/LinearModel"><code>tf.keras.experimental.LinearModel</code></a>。在调用 `Dense` 或 `LinearModel` 之前，应当首先使用 `tf.layers.CategoryEncoding` 对这些输入进行编码，其中 `output_mode='count'`（如果类别大小很大，则为 `sparse=True`）。

## 后续步骤

- 有关 Keras 预处理层的更多信息，请转到[使用预处理层](https://tensorflow.google.cn/guide/keras/preprocessing_layers)指南。
- 有关将预处理层应用于结构化数据的更深入示例，请参阅[使用 Keras 预处理层对结构化数据进行分类](../../tutorials/structured_data/preprocessing_layers.ipynb)教程。